# Group 09 - Automatic Sentence Completion for PubMed

### Authors:
- Constantin Fuerst	
- Leonard Starke

### link to "Attention is All You Need" paper describing transformer models

In [ ]:
https://arxiv.org/pdf/1706.03762.pdf

### load query data from text file 

In [2]:
!wget https://cloud.constantin-fuerst.com/s/944x5BpTQM7GjtF/download -O pubmed-query.txt

--2023-01-18 15:48:24--  https://cloud.constantin-fuerst.com/s/944x5BpTQM7GjtF/download
Loaded CA certificate '/etc/ssl/certs/ca-certificates.crt'
Resolving cloud.constantin-fuerst.com (cloud.constantin-fuerst.com)... 95.91.21.14
Connecting to cloud.constantin-fuerst.com (cloud.constantin-fuerst.com)|95.91.21.14|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1100551 (1.0M) [text/plain]
Saving to: ‘pubmed-query.txt’

pubmed-query.txt    100%[===================>]   1.05M  1.61MB/s    in 0.7s    

2023-01-18 15:48:25 (1.61 MB/s) - ‘pubmed-query.txt’ saved [1100551/1100551]



### import modules used for parsing query data

In [ ]:
try:
    from Bio import Medline
except: 
    !pip install Bio
    from Bio import Medline

### define function for loading the papers from PubMed database

In [1]:
def getPapers(filename):
    pubmed_query = open(filename, encoding='utf-8')
    records = Medline.parse(pubmed_query)
    return list(records)

### Verify that its working

In [4]:
max_records = 150000
records = getPapers("pubmed-query.txt")
records = records[:min(max_records, len(records))]
print(f"Got {len(records)} records from the query text file")

Got 150000 records from the query text file


### Now extract abstracts from records

In [5]:
r_abstracts = []
for r in records:
    if not (r.get('AB') is None):
        r_abstracts.append(r['AB'])

### Now import torch modules needed to load the data

In [6]:
try:
   import torch
   from torch.utils.data import Dataset 
   from torchtext.data import get_tokenizer
except:
   !pip --default-timeout=1000 install torch
   !pip --default-timeout=1000 install torchtext
   import torch
   from torch.utils.data import Dataset 
   from torchtext.data import get_tokenizer

/home/hein/.local/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Import numpy

In [7]:
try:
   import numpy as np
except:
   !pip install numpy
   import numpy as np


### import math module

In [8]:
import math

### define token iterators

In [9]:
train_size = math.floor(len(r_abstracts) * 0.75)
val_size = math.floor(len(r_abstracts) * 0.125)
test_size = math.floor(len(r_abstracts) * 0.125)

In [10]:
def train_abstract_iter():
    for abstract in r_abstracts[:train_size]:
        yield abstract

In [11]:
def val_abstract_iter():
    for abstract in r_abstracts[(train_size + 1):(train_size + val_size)]:
        yield abstract

In [12]:
def test_abstract_iter():
    for abstract in r_abstracts[(train_size + val_size + 1): (train_size + val_size + test_size)]:
        yield abstract

### define Tokenize function

In [13]:
tokenizer = get_tokenizer("basic_english")
def tokenize_abstract_iter():
    for abstract in r_abstracts:
        yield tokenizer(abstract)

### Map every word to an id to store inside torch tensor

In [14]:
from torchtext.vocab import build_vocab_from_iterator
token_generator = tokenize_abstract_iter()
vocab = build_vocab_from_iterator(token_generator, specials=['<unk>'])
vocab.set_default_index(vocab['<unk>'])


### now convert to tensor


In [15]:
def data_process(tokens_iter):
    """Converts raw text into a flat Tensor."""
    data = [torch.tensor(vocab(tokenizer(item)), dtype=torch.long) for item in tokens_iter]
    return torch.cat(tuple(filter(lambda t: t.numel() > 0, data)))

In [16]:
train_generator = train_abstract_iter()
val_generator = val_abstract_iter()
test_generator = test_abstract_iter()
train_data = data_process(train_generator)
val_data = data_process(val_generator)
test_data = data_process(test_generator)

### check gpu

In [20]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [21]:
device

device(type='cuda')

### define model

In [22]:
from typing import Tuple

from torch import nn, Tensor
import torch.nn.functional as F
from torch.nn import TransformerEncoder, TransformerEncoderLayer
from torch.utils.data import dataset

class TransformerModel(nn.Module):

    def __init__(self, ntoken: int, d_model: int, nhead: int, d_hid: int,
                 nlayers: int, dropout: float = 0.5):
        super().__init__()
        self.model_type = 'Transformer'
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        encoder_layers = TransformerEncoderLayer(d_model, nhead, d_hid, dropout)
        self.transformer_encoder = TransformerEncoder(encoder_layers, nlayers)
        self.encoder = nn.Embedding(ntoken, d_model)
        self.d_model = d_model
        self.decoder = nn.Linear(d_model, ntoken)

        self.init_weights()

    def init_weights(self) -> None:
        initrange = 0.1
        self.encoder.weight.data.uniform_(-initrange, initrange)
        self.decoder.bias.data.zero_()
        self.decoder.weight.data.uniform_(-initrange, initrange)

    def forward(self, src: Tensor, src_mask: Tensor) -> Tensor:
        """
        Args:
            src: Tensor, shape [seq_len, batch_size]
            src_mask: Tensor, shape [seq_len, seq_len]

        Returns:
            output Tensor of shape [seq_len, batch_size, ntoken]
        """
        src = self.encoder(src) * math.sqrt(self.d_model)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src, src_mask)
        output = self.decoder(output)
        return output


def generate_square_subsequent_mask(sz: int) -> Tensor:
    """Generates an upper-triangular matrix of -inf, with zeros on diag."""
    return torch.triu(torch.ones(sz, sz) * float('-inf'), diagonal=1)

### define pos encoder

In [23]:
class PositionalEncoding(nn.Module):

    def __init__(self, d_model: int, dropout: float = 0.1, max_len: int = 5000):
        super().__init__()
        self.dropout = nn.Dropout(p=dropout)

        position = torch.arange(max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2) * (-math.log(10000.0) / d_model))
        pe = torch.zeros(max_len, 1, d_model)
        pe[:, 0, 0::2] = torch.sin(position * div_term)
        pe[:, 0, 1::2] = torch.cos(position * div_term)
        self.register_buffer('pe', pe)

    def forward(self, x: Tensor) -> Tensor:
        """
        Args:
            x: Tensor, shape [seq_len, batch_size, embedding_dim]
        """
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)


### define function to create batches of data and create batches

In [24]:
def batchify(data: Tensor, bsz: int) -> Tensor:
    """Divides the data into bsz separate sequences, removing extra elements
    that wouldn't cleanly fit.

    Args:
        data: Tensor, shape [N]
        bsz: int, batch size

    Returns:
        Tensor of shape [N // bsz, bsz]
    """
    seq_len = data.size(0) // bsz
    data = data[:seq_len * bsz]
    data = data.view(bsz, seq_len).t().contiguous()
    return data.to(device)

In [25]:
batch_size = 20
eval_batch_size = 10
train_data = batchify(train_data, batch_size)  # shape [seq_len, batch_size]
val_data = batchify(val_data, eval_batch_size)
test_data = batchify(test_data, eval_batch_size)

### define function to get batch

In [26]:
bptt = 35
def get_batch(source: Tensor, i: int) -> Tuple[Tensor, Tensor]:
    """
    Args:
        source: Tensor, shape [full_seq_len, batch_size]
        i: int

    Returns:
        tuple (data, target), where data has shape [seq_len, batch_size] and
        target has shape [seq_len * batch_size]
    """
    seq_len = min(bptt, len(source) - 1 - i)
    data = source[i:i+seq_len]
    target = source[i+1:i+1+seq_len].reshape(-1)
    return data, target

### define parameters and init model

In [27]:
ntokens = len(vocab)  # size of vocabulary
emsize = 200  # embedding dimension
d_hid = 200  # dimension of the feedforward network model in nn.TransformerEncoder
nlayers = 2  # number of nn.TransformerEncoderLayer in nn.TransformerEncoder
nhead = 2  # number of heads in nn.MultiheadAttention
dropout = 0.2  # dropout probability
model = TransformerModel(ntokens, emsize, nhead, d_hid, nlayers, dropout).to(device)

### init optimizer, loss, scheduler etc.

In [28]:
import copy
import time

criterion = nn.CrossEntropyLoss()
lr = 5.0  # learning rate
optimizer = torch.optim.SGD(model.parameters(), lr=lr)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, 1.0, gamma=0.95)

### define train function

In [29]:
def train(model: nn.Module) -> None:
    model.train()  # turn on train mode
    total_loss = 0.
    log_interval = 200
    start_time = time.time()
    src_mask = generate_square_subsequent_mask(bptt).to(device)

    num_batches = len(train_data) // bptt
    for batch, i in enumerate(range(0, train_data.size(0) - 1, bptt)):
        data, targets = get_batch(train_data, i)
        seq_len = data.size(0)
        if seq_len != bptt:  # only on last batch
            src_mask = src_mask[:seq_len, :seq_len]
        output = model(data, src_mask)
        loss = criterion(output.view(-1, ntokens), targets)

        optimizer.zero_grad()
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 0.5)
        optimizer.step()

        total_loss += loss.item()
        if batch % log_interval == 0 and batch > 0:
            lr = scheduler.get_last_lr()[0]
            ms_per_batch = (time.time() - start_time) * 1000 / log_interval
            cur_loss = total_loss / log_interval
            ppl = math.exp(cur_loss)
            print(f'| epoch {epoch:3d} | {batch:5d}/{num_batches:5d} batches | '
                  f'lr {lr:02.2f} | ms/batch {ms_per_batch:5.2f} | '
                  f'loss {cur_loss:5.2f} | ppl {ppl:8.2f}')
            total_loss = 0
            start_time = time.time()

### define evaluate function

In [30]:
def evaluate(model: nn.Module, eval_data: Tensor) -> float:
    model.eval()  # turn on evaluation mode
    total_loss = 0.
    src_mask = generate_square_subsequent_mask(bptt).to(device)
    with torch.no_grad():
        for i in range(0, eval_data.size(0) - 1, bptt):
            data, targets = get_batch(eval_data, i)
            seq_len = data.size(0)
            if seq_len != bptt:
                src_mask = src_mask[:seq_len, :seq_len]
            output = model(data, src_mask)
            output_flat = output.view(-1, ntokens)
            total_loss += seq_len * criterion(output_flat, targets).item()
    return total_loss / (len(eval_data) - 1)

### now we can start training the model while saving best one

In [31]:
best_val_loss = float('inf')
epochs = 10
best_model = None

for epoch in range(1, epochs + 1):
    epoch_start_time = time.time()
    train(model)
    val_loss = evaluate(model, val_data)
    val_ppl = math.exp(val_loss)
    elapsed = time.time() - epoch_start_time
    print('-' * 89)
    print(f'| end of epoch {epoch:3d} | time: {elapsed:5.2f}s | '
          f'valid loss {val_loss:5.2f} | valid ppl {val_ppl:8.2f}')
    print('-' * 89)

    if val_loss < best_val_loss:
        best_val_loss = val_loss
        best_model = copy.deepcopy(model)

    scheduler.step()

| epoch   1 |   200/13484 batches | lr 5.00 | ms/batch 116.24 | loss  9.27 | ppl 10651.55
| epoch   1 |   400/13484 batches | lr 5.00 | ms/batch 114.02 | loss  7.49 | ppl  1787.62
| epoch   1 |   600/13484 batches | lr 5.00 | ms/batch 114.33 | loss  6.83 | ppl   923.44
| epoch   1 |   800/13484 batches | lr 5.00 | ms/batch 114.54 | loss  6.54 | ppl   693.98
| epoch   1 |  1000/13484 batches | lr 5.00 | ms/batch 114.73 | loss  6.33 | ppl   563.29
| epoch   1 |  1200/13484 batches | lr 5.00 | ms/batch 114.85 | loss  6.18 | ppl   485.05
| epoch   1 |  1400/13484 batches | lr 5.00 | ms/batch 114.91 | loss  6.09 | ppl   440.69
| epoch   1 |  1600/13484 batches | lr 5.00 | ms/batch 115.00 | loss  6.06 | ppl   428.38
| epoch   1 |  1800/13484 batches | lr 5.00 | ms/batch 115.17 | loss  5.98 | ppl   397.07
| epoch   1 |  2000/13484 batches | lr 5.00 | ms/batch 115.17 | loss  5.91 | ppl   369.13
| epoch   1 |  2200/13484 batches | lr 5.00 | ms/batch 115.22 | loss  5.89 | ppl   360.14
| epoch   

| epoch   2 |  4600/13484 batches | lr 4.75 | ms/batch 115.18 | loss  5.35 | ppl   210.15
| epoch   2 |  4800/13484 batches | lr 4.75 | ms/batch 115.24 | loss  5.32 | ppl   204.37
| epoch   2 |  5000/13484 batches | lr 4.75 | ms/batch 115.29 | loss  5.33 | ppl   205.42
| epoch   2 |  5200/13484 batches | lr 4.75 | ms/batch 115.24 | loss  5.31 | ppl   201.44
| epoch   2 |  5400/13484 batches | lr 4.75 | ms/batch 115.23 | loss  5.30 | ppl   200.48
| epoch   2 |  5600/13484 batches | lr 4.75 | ms/batch 115.26 | loss  5.29 | ppl   197.76
| epoch   2 |  5800/13484 batches | lr 4.75 | ms/batch 115.22 | loss  5.34 | ppl   207.65
| epoch   2 |  6000/13484 batches | lr 4.75 | ms/batch 115.11 | loss  5.32 | ppl   204.89
| epoch   2 |  6200/13484 batches | lr 4.75 | ms/batch 115.22 | loss  5.34 | ppl   209.24
| epoch   2 |  6400/13484 batches | lr 4.75 | ms/batch 115.14 | loss  5.31 | ppl   201.48
| epoch   2 |  6600/13484 batches | lr 4.75 | ms/batch 115.20 | loss  5.36 | ppl   212.87
| epoch   

| epoch   3 |  9000/13484 batches | lr 4.51 | ms/batch 115.21 | loss  5.21 | ppl   182.88
| epoch   3 |  9200/13484 batches | lr 4.51 | ms/batch 115.28 | loss  5.21 | ppl   183.47
| epoch   3 |  9400/13484 batches | lr 4.51 | ms/batch 115.22 | loss  5.22 | ppl   184.25
| epoch   3 |  9600/13484 batches | lr 4.51 | ms/batch 115.27 | loss  5.18 | ppl   177.24
| epoch   3 |  9800/13484 batches | lr 4.51 | ms/batch 115.25 | loss  5.16 | ppl   174.24
| epoch   3 | 10000/13484 batches | lr 4.51 | ms/batch 115.22 | loss  5.21 | ppl   182.29
| epoch   3 | 10200/13484 batches | lr 4.51 | ms/batch 115.13 | loss  5.17 | ppl   175.34
| epoch   3 | 10400/13484 batches | lr 4.51 | ms/batch 115.28 | loss  5.14 | ppl   170.79
| epoch   3 | 10600/13484 batches | lr 4.51 | ms/batch 115.20 | loss  5.17 | ppl   176.55
| epoch   3 | 10800/13484 batches | lr 4.51 | ms/batch 115.24 | loss  5.22 | ppl   185.77
| epoch   3 | 11000/13484 batches | lr 4.51 | ms/batch 115.23 | loss  5.19 | ppl   179.38
| epoch   

| epoch   4 | 13400/13484 batches | lr 4.29 | ms/batch 115.28 | loss  5.12 | ppl   166.66
-----------------------------------------------------------------------------------------
| end of epoch   4 | time: 1626.36s | valid loss  5.13 | valid ppl   168.54
-----------------------------------------------------------------------------------------
| epoch   5 |   200/13484 batches | lr 4.07 | ms/batch 115.90 | loss  5.14 | ppl   170.65
| epoch   5 |   400/13484 batches | lr 4.07 | ms/batch 115.23 | loss  5.09 | ppl   163.18
| epoch   5 |   600/13484 batches | lr 4.07 | ms/batch 115.19 | loss  5.07 | ppl   159.22
| epoch   5 |   800/13484 batches | lr 4.07 | ms/batch 115.17 | loss  5.08 | ppl   160.60
| epoch   5 |  1000/13484 batches | lr 4.07 | ms/batch 115.25 | loss  5.08 | ppl   160.49
| epoch   5 |  1200/13484 batches | lr 4.07 | ms/batch 115.15 | loss  5.07 | ppl   158.86
| epoch   5 |  1400/13484 batches | lr 4.07 | ms/batch 115.14 | loss  5.06 | ppl   156.88
| epoch   5 |  1600/1348

| epoch   6 |  3800/13484 batches | lr 3.87 | ms/batch 115.20 | loss  5.00 | ppl   148.07
| epoch   6 |  4000/13484 batches | lr 3.87 | ms/batch 115.32 | loss  4.94 | ppl   140.04
| epoch   6 |  4200/13484 batches | lr 3.87 | ms/batch 115.21 | loss  4.97 | ppl   144.64
| epoch   6 |  4400/13484 batches | lr 3.87 | ms/batch 115.20 | loss  4.99 | ppl   146.48
| epoch   6 |  4600/13484 batches | lr 3.87 | ms/batch 115.18 | loss  5.03 | ppl   153.49
| epoch   6 |  4800/13484 batches | lr 3.87 | ms/batch 115.30 | loss  5.01 | ppl   150.20
| epoch   6 |  5000/13484 batches | lr 3.87 | ms/batch 115.24 | loss  5.00 | ppl   148.23
| epoch   6 |  5200/13484 batches | lr 3.87 | ms/batch 115.22 | loss  5.00 | ppl   148.51
| epoch   6 |  5400/13484 batches | lr 3.87 | ms/batch 115.31 | loss  4.98 | ppl   145.45
| epoch   6 |  5600/13484 batches | lr 3.87 | ms/batch 115.25 | loss  4.99 | ppl   146.84
| epoch   6 |  5800/13484 batches | lr 3.87 | ms/batch 115.29 | loss  4.99 | ppl   147.24
| epoch   

| epoch   7 |  8200/13484 batches | lr 3.68 | ms/batch 115.26 | loss  4.92 | ppl   136.77
| epoch   7 |  8400/13484 batches | lr 3.68 | ms/batch 115.33 | loss  4.94 | ppl   139.78
| epoch   7 |  8600/13484 batches | lr 3.68 | ms/batch 115.31 | loss  4.95 | ppl   141.01
| epoch   7 |  8800/13484 batches | lr 3.68 | ms/batch 115.18 | loss  4.93 | ppl   138.80
| epoch   7 |  9000/13484 batches | lr 3.68 | ms/batch 115.19 | loss  4.95 | ppl   141.73
| epoch   7 |  9200/13484 batches | lr 3.68 | ms/batch 115.23 | loss  4.97 | ppl   144.05
| epoch   7 |  9400/13484 batches | lr 3.68 | ms/batch 115.24 | loss  4.97 | ppl   144.66
| epoch   7 |  9600/13484 batches | lr 3.68 | ms/batch 115.26 | loss  4.93 | ppl   138.12
| epoch   7 |  9800/13484 batches | lr 3.68 | ms/batch 115.27 | loss  4.91 | ppl   135.39
| epoch   7 | 10000/13484 batches | lr 3.68 | ms/batch 115.19 | loss  4.94 | ppl   140.12
| epoch   7 | 10200/13484 batches | lr 3.68 | ms/batch 115.27 | loss  4.90 | ppl   134.73
| epoch   

| epoch   8 | 12600/13484 batches | lr 3.49 | ms/batch 115.31 | loss  4.86 | ppl   128.83
| epoch   8 | 12800/13484 batches | lr 3.49 | ms/batch 115.24 | loss  4.88 | ppl   131.60
| epoch   8 | 13000/13484 batches | lr 3.49 | ms/batch 115.33 | loss  4.87 | ppl   130.10
| epoch   8 | 13200/13484 batches | lr 3.49 | ms/batch 115.29 | loss  4.88 | ppl   131.87
| epoch   8 | 13400/13484 batches | lr 3.49 | ms/batch 115.40 | loss  4.90 | ppl   134.29
-----------------------------------------------------------------------------------------
| end of epoch   8 | time: 1626.66s | valid loss  5.00 | valid ppl   148.39
-----------------------------------------------------------------------------------------
| epoch   9 |   200/13484 batches | lr 3.32 | ms/batch 115.97 | loss  4.92 | ppl   136.72
| epoch   9 |   400/13484 batches | lr 3.32 | ms/batch 115.40 | loss  4.88 | ppl   131.62
| epoch   9 |   600/13484 batches | lr 3.32 | ms/batch 115.30 | loss  4.85 | ppl   128.22
| epoch   9 |   800/1348

| epoch  10 |  3000/13484 batches | lr 3.15 | ms/batch 115.36 | loss  4.81 | ppl   122.12
| epoch  10 |  3200/13484 batches | lr 3.15 | ms/batch 115.44 | loss  4.79 | ppl   120.18
| epoch  10 |  3400/13484 batches | lr 3.15 | ms/batch 115.43 | loss  4.84 | ppl   127.05
| epoch  10 |  3600/13484 batches | lr 3.15 | ms/batch 115.39 | loss  4.82 | ppl   123.70
| epoch  10 |  3800/13484 batches | lr 3.15 | ms/batch 115.40 | loss  4.80 | ppl   121.74
| epoch  10 |  4000/13484 batches | lr 3.15 | ms/batch 115.49 | loss  4.76 | ppl   116.53
| epoch  10 |  4200/13484 batches | lr 3.15 | ms/batch 115.42 | loss  4.78 | ppl   119.64
| epoch  10 |  4400/13484 batches | lr 3.15 | ms/batch 115.36 | loss  4.80 | ppl   121.17
| epoch  10 |  4600/13484 batches | lr 3.15 | ms/batch 115.42 | loss  4.84 | ppl   126.61
| epoch  10 |  4800/13484 batches | lr 3.15 | ms/batch 115.43 | loss  4.83 | ppl   124.71
| epoch  10 |  5000/13484 batches | lr 3.15 | ms/batch 115.39 | loss  4.81 | ppl   122.89
| epoch  1

### print info about best model after training

In [32]:
test_loss = evaluate(best_model, test_data)
test_ppl = math.exp(test_loss)
print('=' * 89)
print(f'| End of training | test loss {test_loss:5.2f} | '
      f'test ppl {test_ppl:8.2f}')
print('=' * 89)

| End of training | test loss  4.98 | test ppl   144.89


### save trained model to file

In [33]:
torch.save(best_model, "pubmed-sentencecomplete.pt")

## Now we can try to predict based on trained model

### obtain iterator for predict batch 

In [159]:
def predict_abstract_iter(batch):
    for batch in batch:
        yield tokenizer(batch)

### load data into tensor for model to process

In [154]:
def toDataTensor(batch):
    predict_generator = predict_abstract_iter(batch)
    return [torch.tensor(vocab.lookup_indices(item)) for item in predict_generator]

### check device once again (prob not needed)

In [7]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

NameError: name 'torch' is not defined

### optionally load model from file if it was trained already

In [50]:
best_model = torch.load("pubmed-sentencecomplete.pt")
best_model.eval()

TransformerModel(
  (pos_encoder): PositionalEncoding(
    (dropout): Dropout(p=0.2, inplace=False)
  )
  (transformer_encoder): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=200, out_features=200, bias=True)
        )
        (linear1): Linear(in_features=200, out_features=200, bias=True)
        (dropout): Dropout(p=0.2, inplace=False)
        (linear2): Linear(in_features=200, out_features=200, bias=True)
        (norm1): LayerNorm((200,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((200,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.2, inplace=False)
        (dropout2): Dropout(p=0.2, inplace=False)
      )
      (1): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=200, out_features=200, bias=True)
        )
        

### define predict function

In [160]:
def predict(input_line, mask, n_predictions=3):
    with torch.no_grad():
        output = best_model(input_line.to(device), mask)        
        predictions = []
        for i in range(n_predictions):
            next_item = output.topk(i+1)[1].view(-1)[-1].item()
            predict_token_index = next_item
            predictions.append(vocab.lookup_token(predict_token_index))
        
        return predictions

### define input batch 

In [2]:
sample_batch = [
               "There is"
]
input_batch = sample_batch

### define initial source mask for model

In [3]:
bptt = 2
src_mask = generate_square_subsequent_mask(bptt).to(device)

NameError: name 'generate_square_subsequent_mask' is not defined

### Execute prediction and display predicted values and choose continuation

In [4]:
def predict_loop(num_of_pred):
    iteration = 0
    is_terminated = False
    input_batch = sample_batch
    while(not is_terminated):
        mask_size = bptt+(iteration)     
        src_mask = generate_square_subsequent_mask(mask_size).to(device)
        data = toDataTensor(input_batch)
        
        for i, d in enumerate(data):
            predictions = predict(d, src_mask, num_of_pred)
            
            print("\n Possible continuations:")
            for j in range(len(predictions)):
                print(j + 1, ": ", predictions[j])
            s_index = input(input_batch[i])
            if("e" in s_index):
                is_terminated = True
                print("prediction stopped.")
                break

            print("Text is now:")
            input_batch[i] += (" " + predictions[int(s_index) - 1])
            print(input_batch[i])

        iteration = iteration + 1

In [5]:
predict_loop(3)

NameError: name 'generate_square_subsequent_mask' is not defined